## astroquery ##
#### One easy way to harness "the internet" with Python ...####

4 real life cases:

- 1)  update a list of telluric stars
- 2a) check the WCS solution of a MUSE cube
- 2b) drizzle HST images onto a proper grid
- 4)  find all the "SKY" fields observed by MUSE

## 1) Custom Simbad query ##

In [5]:
from astroquery.simbad import Simbad
Simbad.ROW_LIMIT = 15 # now any query fetches at most 15 rows

from astropy.coordinates import FK5
from astropy.coordinates import SkyCoord
import astropy.units as u

# Set up the SIMBAD call
customSimbad0 = Simbad()
customSimbad0.add_votable_fields('ra(2;A;ICRS;J2017.5;2000)',
                                 'dec(2;D;ICRS;J2017.5;2000)',
                                 'flux(V)','flux(I)','flux(J)','flux(H)','flux(K)',
                                 'sp', 'otype(3)')
customSimbad0.remove_votable_fields('coordinates')

# Send the query !
r0 = customSimbad0.query_object('Hip089551')
r0.pprint()

# Now, do a search by coordinates as well
c = SkyCoord('18h16m22.2020s 10d48m53.153s',frame=FK5)
print ' '
r1 = customSimbad0.query_region(c, radius=10*u.arcmin)
r1.pprint()

 MAIN_ID  RA_2_A_ICRS_J2017_5_2000 DEC_2_D_ICRS_J2017_5_2000 ... SP_TYPE OTYPE_3
                  "h:m:s"                   "d:m:s"          ...                
--------- ------------------------ ------------------------- ... ------- -------
HD 167785            18 16 22.2020             +10 48 53.153 ...     B2V       *
 
        MAIN_ID         RA_2_A_ICRS_J2017_5_2000 ... SP_TYPE OTYPE_3
                                "h:m:s"          ...                
----------------------- ------------------------ ... ------- -------
              HD 167785            18 16 22.2020 ...     B2V       *
          TYC 1014-45-1            18 16 31.9008 ...               *
         TYC 1014-283-1             18 16 18.532 ...               *
         TYC 1014-569-1             18 16 05.216 ...               *
         TYC 1014-465-1            18 16 13.3392 ...               *
         TYC 1014-695-1            18 16 40.2338 ...               *
2MASX J18162582+1054215             18 16 25.825 ... 

## 2a+b) Get all the GAIA DR1 stars around a target  ##

In [6]:
import astropy.units as u
from astropy.coordinates.sky_coordinate import SkyCoord
from astropy.units import Quantity
from astroquery.gaia import Gaia

target_coord = SkyCoord(ra='01h04m03.0s', dec='-72d02m00.000s', frame='icrs')
search_radius = Quantity(2.5, u.arcmin)

# Make it a sync search, because I don't think I need more than 2000 targets ...
j = Gaia.cone_search(target_coord, search_radius)
r = j.get_results()
r['ra','dec','phot_g_mean_mag'].pprint()

Launched query: 'SELECT  TOP 2000 DISTANCE(POINT('ICRS',ra,dec),             POINT('ICRS',16.0124878257,-72.0333324285)) AS dist, *             FROM gaiadr1.gaia_source WHERE CONTAINS(            POINT('ICRS',ra,dec),            CIRCLE('ICRS',16.0124878257,-72.0333324285, 0.0416666666667))=1             ORDER BY dist ASC'
Retrieving sync. results...
Query finished.
        ra                 dec          phot_g_mean_mag  
    Angle[deg]          Angle[deg]       Magnitude[mag]  
------------------ ------------------- ------------------
16.011509115204813 -72.032280132860222 17.901667686919737
16.006894381348374 -72.031814726946351  20.46190717870785
16.005081178931089 -72.032645287753965 16.525449483858822
16.016960810442814 -72.035318888108321 19.248231538365758
16.022509820289073  -72.03249448264944 18.585163348881821
16.001962494319109 -72.032663083815578 20.036524778555325
 16.00821002544966 -72.030167993721477 19.213980429292889
16.020367279660153 -72.030830270697024 18.1338259776


<img src="MUSE_vs_GAIA.png" style="width: 600px;">

## 3) Query the ESO archive ##

In [8]:
from astroquery.eso import Eso
from astropy.coordinates import SkyCoord
from astropy.coordinates import Galactic, FK5
import astropy.units as u
import numpy as np

eso = Eso()
eso.ROW_LIMIT=-1 # Remove the upper limits to the query ... for some reason, this is still capped to 1e4 ...

# Now query the archive ... that's magic !
table_muse = eso.query_instrument('muse', column_filters={'dp_cat':'SCIENCE',
                                                     #'dp_type':'SCIENCE',
                                                     'dp_type':'SKY',
                                                     'stime':'2014-01-01', 
                                                     'etime':'2017-05-01',
                                                     #'prog_type':'1',
                                                     'pi_coi':'ANDERSON',
                                                     },
                                          #columns={
                                                     #row_limit=1e6
                                                     )

print 'Number of individual MUSE skies: %i' % (len(table_muse))

# Extract the coordinates
muse_target_radec = SkyCoord(list(table_muse['Target Ra Dec']),FK5,unit=(u.hourangle,u.deg))

# Cross match the sources with themselves. Look for anything close-by (10 arcsec)
idxc, idxcatalog, d2d, d3d = muse_target_radec.search_around_sky(muse_target_radec,10*u.arcsec)

# Then, make a list of all the groups (with each group listed only once)
groups = []
for (i,id) in enumerate(np.unique(idxc)):
   if not(idxcatalog[idxc==id].tolist() in groups):
      groups.append(idxcatalog[idxc==id].tolist())

print 'Number of individual MUSE sky locations: %i' % (len(groups))

Number of individual MUSE skies: 156
Number of individual MUSE sky locations: 72


<img src="MUSE_sky_fields_locations.png">
<img src="MUSE_sky_fields.png" style="width: 600px;">